<a href="https://colab.research.google.com/github/askewai/git/blob/main/latihanTextMining_bs.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [14]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
import re
import string
import nltk
from nltk.tokenize import word_tokenize
from collections import Counter

In [15]:
# API Scraper
SCRAPER_API_KEY = "64c39b9d586a9a9ffb12f47b655d633d"
SCRAPER_API_URL = "http://api.scraperapi.com"

In [16]:
import time

# Fungsi untuk mengambil review dari satu halaman
def get_reviews_from_page(url):
    target_url = f"{SCRAPER_API_URL}?api_key={SCRAPER_API_KEY}&url={url}&render=true"
    headers = {"User-Agent": "Mozilla/5.0"}

    response = requests.get(target_url, headers=headers)
    soup = BeautifulSoup(response.text, "html.parser")

    reviews = []
    for review_section in soup.find_all("article", class_="ReviewCard"):
        review_text = review_section.find("span", class_="Formatted")
        if review_text:
            reviews.append(review_text.get_text().strip())

    return reviews, soup

# Mulai scraping dengan pagination
all_reviews = []
base_url = "https://www.goodreads.com/book/show/32528129/reviews"

page = 1
while True:
    print(f"Scraping halaman {page}...")

    # Buat URL dengan parameter halaman
    paginated_url = f"{base_url}?page={page}"

    # Ambil review dari halaman tersebut
    reviews, soup = get_reviews_from_page(paginated_url)

    # Jika tidak ada review baru, berarti sudah mencapai akhir
    if not reviews:
        print("Tidak ada review baru, scraping selesai.")
        break

    # Tambahkan review ke list utama
    all_reviews.extend(reviews)

    # Tambahkan jeda untuk menghindari pemblokiran
    time.sleep(2)

    # Pindah ke halaman berikutnya
    page += 1

# Simpan hasil ke DataFrame
df = pd.DataFrame({"full_text": all_reviews})

Scraping halaman 1...
Scraping halaman 2...
Scraping halaman 3...
Scraping halaman 4...
Scraping halaman 5...
Scraping halaman 6...
Scraping halaman 7...
Scraping halaman 8...
Scraping halaman 9...
Scraping halaman 10...
Scraping halaman 11...
Scraping halaman 12...
Scraping halaman 13...
Scraping halaman 14...
Scraping halaman 15...
Scraping halaman 16...
Scraping halaman 17...
Scraping halaman 18...
Scraping halaman 19...
Scraping halaman 20...
Scraping halaman 21...
Scraping halaman 22...
Scraping halaman 23...
Scraping halaman 24...
Scraping halaman 25...
Scraping halaman 26...
Scraping halaman 27...
Scraping halaman 28...
Scraping halaman 29...
Scraping halaman 30...
Scraping halaman 31...
Scraping halaman 32...
Scraping halaman 33...
Scraping halaman 34...
Scraping halaman 35...
Scraping halaman 36...
Scraping halaman 37...
Scraping halaman 38...
Scraping halaman 39...
Scraping halaman 40...
Scraping halaman 41...
Scraping halaman 42...
Scraping halaman 43...
Scraping halaman 44.

In [17]:
# Tampilkan jumlah review yang berhasil diambil
print(f"Total review yang dikumpulkan: {len(all_reviews)}")
df.head()

Total review yang dikumpulkan: 2190


full_text
0  "Kenapa jatuh cinta itu sakit? Karena lo membe...
1  Just not my cup of tea. Beda banget banget ban...
2  Ketika membaca halaman awal, vibesnya terasa m...
3  Lima bintang untuk buku ini :) Selalu suka sam...
4  Ceritanya sederhana. Tentang dua orang yang sa...

In [18]:
print(df.to_string())

In [19]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2190 entries, 0 to 2189
Data columns (total 1 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   full_text  2190 non-null   object
dtypes: object(1)
memory usage: 17.2+ KB


In [20]:
# Step 2: Konversi ke huruf kecil
def casefoldingText(text):
    return text.lower()

df['caseFolded_fullText'] = df['full_text'].apply(casefoldingText)

In [21]:
df.head()

full_text  \
0  "Kenapa jatuh cinta itu sakit? Karena lo membe...   
1  Just not my cup of tea. Beda banget banget ban...   
2  Ketika membaca halaman awal, vibesnya terasa m...   
3  Lima bintang untuk buku ini :) Selalu suka sam...   
4  Ceritanya sederhana. Tentang dua orang yang sa...   

                                 caseFolded_fullText  
0  "kenapa jatuh cinta itu sakit? karena lo membe...  
1  just not my cup of tea. beda banget banget ban...  
2  ketika membaca halaman awal, vibesnya terasa m...  
3  lima bintang untuk buku ini :) selalu suka sam...  
4  ceritanya sederhana. tentang dua orang yang sa...

In [22]:
# Step 3: Pembersihan teks dengan regex
def cleaningText(text):
    text = re.sub(r'@[A-Za-z0-9_]+', '', text)  # Hapus mentions
    text = re.sub(r'#[A-Za-z0-9_]+', '', text)  # Hapus hashtag
    text = re.sub(r'RT\s+', '', text)  # Hapus RT
    text = re.sub(r'http\S+', '', text)  # Hapus link
    text = re.sub(r'[^A-Za-z ]+', '', text)  # Hapus karakter non-alfabet
    text = text.replace('\n', ' ')  # Ganti newline dengan spasi
    text = text.translate(str.maketrans('', '', string.punctuation))  # Hapus tanda baca
    text = text.strip()  # Hapus spasi di awal dan akhir
    return text

df['cleaning'] = df['caseFolded_fullText'].apply(cleaningText)

In [23]:
df.head()

full_text  \
0  "Kenapa jatuh cinta itu sakit? Karena lo membe...   
1  Just not my cup of tea. Beda banget banget ban...   
2  Ketika membaca halaman awal, vibesnya terasa m...   
3  Lima bintang untuk buku ini :) Selalu suka sam...   
4  Ceritanya sederhana. Tentang dua orang yang sa...   

                                 caseFolded_fullText  \
0  "kenapa jatuh cinta itu sakit? karena lo membe...   
1  just not my cup of tea. beda banget banget ban...   
2  ketika membaca halaman awal, vibesnya terasa m...   
3  lima bintang untuk buku ini :) selalu suka sam...   
4  ceritanya sederhana. tentang dua orang yang sa...   

                                            cleaning  
0  kenapa jatuh cinta itu sakit karena lo memberi...  
1  just not my cup of tea beda banget banget bang...  
2  ketika membaca halaman awal vibesnya terasa mi...  
3  lima bintang untuk buku ini  selalu suka sama ...  
4  ceritanya sederhana tentang dua orang yang sal...

In [24]:
# Step 4: Tokenisasi
def tokenizingText(text):
    return text.split()

df['tokenizing'] = df['cleaning'].apply(tokenizingText)

In [25]:
df.head()

full_text  \
0  "Kenapa jatuh cinta itu sakit? Karena lo membe...   
1  Just not my cup of tea. Beda banget banget ban...   
2  Ketika membaca halaman awal, vibesnya terasa m...   
3  Lima bintang untuk buku ini :) Selalu suka sam...   
4  Ceritanya sederhana. Tentang dua orang yang sa...   

                                 caseFolded_fullText  \
0  "kenapa jatuh cinta itu sakit? karena lo membe...   
1  just not my cup of tea. beda banget banget ban...   
2  ketika membaca halaman awal, vibesnya terasa m...   
3  lima bintang untuk buku ini :) selalu suka sam...   
4  ceritanya sederhana. tentang dua orang yang sa...   

                                            cleaning  \
0  kenapa jatuh cinta itu sakit karena lo memberi...   
1  just not my cup of tea beda banget banget bang...   
2  ketika membaca halaman awal vibesnya terasa mi...   
3  lima bintang untuk buku ini  selalu suka sama ...   
4  ceritanya sederhana tentang dua orang yang sal...   

                                          tokenizing  
0  [kenapa, jatuh, cinta, itu, sakit, karena, lo,...  
1  [just, not, my, cup, of, tea, beda, banget, ba...  
2  [ketika, membaca, halaman, awal, vibesnya, ter...  
3  [lima, bintang, untuk, buku, ini, selalu, suka...  
4  [ceritanya, sederhana, tentang, dua, orang, ya...

In [26]:
# Step 5: Mencari kata yang sering muncul
all_words = [word for tokens in df['tokenizing'] for word in tokens]
word_freq = Counter(all_words)
most_common_words = word_freq.most_common(10)  # 10 kata yang paling sering muncul

In [27]:
# Menampilkan hasil
df.head(), most_common_words

(                                           full_text  \
 0  "Kenapa jatuh cinta itu sakit? Karena lo membe...   
 1  Just not my cup of tea. Beda banget banget ban...   
 2  Ketika membaca halaman awal, vibesnya terasa m...   
 3  Lima bintang untuk buku ini :) Selalu suka sam...   
 4  Ceritanya sederhana. Tentang dua orang yang sa...   
 
                                  caseFolded_fullText  \
 0  "kenapa jatuh cinta itu sakit? karena lo membe...   
 1  just not my cup of tea. beda banget banget ban...   
 2  ketika membaca halaman awal, vibesnya terasa m...   
 3  lima bintang untuk buku ini :) selalu suka sam...   
 4  ceritanya sederhana. tentang dua orang yang sa...   
 
                                             cleaning  \
 0  kenapa jatuh cinta itu sakit karena lo memberi...   
 1  just not my cup of tea beda banget banget bang...   
 2  ketika membaca halaman awal vibesnya terasa mi...   
 3  lima bintang untuk buku ini  selalu suka sama ...   
 4  ceritanya sederhana ten

In [28]:
# Simpan DataFrame ke file CSV
df.to_csv('reviews_data.csv', index=False)

print("Data telah disimpan ke 'reviews_data.csv'")

Data telah disimpan ke 'reviews_data.csv'
